# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [20]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv('../Vacation_Search/WeatherPy_vacation.csv')

# Display sample data
vacation_df

City_ID              City Country  Max Temp      Lat       Lng  \
0         1           Cayenne      GF     84.24   4.9333  -52.3333   
1         2              Lamu      KE     80.82  -2.2717   40.9020   
2        10      Saint-Pierre      RE     80.56 -21.3393   55.4781   
3        16    Cabo San Lucas      MX     83.61  22.8909 -109.9124   
4        27              Uaua      BR     82.35  -9.8414  -39.4817   
..      ...               ...     ...       ...      ...       ...   
64      672          Acapulco      MX     89.42  16.8634  -99.8901   
65      674          Paracuru      BR     81.10  -3.4100  -39.0306   
66      679  Puerto Maldonado      PE     86.67 -12.6000  -69.1833   
67      682           Pitimbu      BR     84.79  -7.4706  -34.8086   
68      685      Bull Savanna      JM     83.35  17.8868  -77.5902   

         Description                                 Hotel Name  
0   scattered clouds                              Central Hôtel  
1    overcast clouds  Hotel Archipelago villa bed and breakfast  
2          clear sky                               Tropic Hotel  
3         few clouds                              Comfort Rooms  
4      moderate rain                                 Hotel Uauá  
..               ...                                        ...  
64         clear sky                            Hotel del Valle  
65     broken clouds                          Pousada Sol e Lua  
66     moderate rain                            Puerto Palmeras  
67  scattered clouds                          Pousada Brisa Mar  
68         clear sky                       Junction Guest House  

[69 rows x 8 columns]

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [5]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name","Country","Current Description"]

)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [31]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"] == "Bonoua"]
vacation_end = vacation_df.loc[vacation_df["City"] == "Sapele"]
vacation_stop1 = vacation_df.loc[vacation_df["City"] == "Anloga"]
vacation_stop2 = vacation_df.loc[vacation_df["City"] == "Porto Novo"]
vacation_stop3 = vacation_df.loc[vacation_df["City"] == "Bonouo"]

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [32]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
destinations = [vacation_start, vacation_end, vacation_stop1, vacation_stop2, vacation_stop3]
itinerary_df = pd.concat(destinations)

# Display sample data
itinerary_df


City_ID        City Country  Max Temp     Lat     Lng      Description  \
10      101      Bonoua      CI     82.02  5.2741 -3.5950  overcast clouds   
37      453      Sapele      NG     81.43  5.8941  5.6767    broken clouds   
33      429      Anloga      GH     82.35  5.7947  0.8973  overcast clouds   
53      602  Porto Novo      BJ     82.22  6.4965  2.6036  overcast clouds   

                Hotel Name  
10           Aliekro Hôtel  
37  Hamsphare hotel sapele  
33    Hotel de White House  
53          Hôtel 6500 CFA

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [33]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[["Lng","Lat"]].copy()

# Display sample data
waypoints_df

Lng     Lat
10 -3.5950  5.2741
37  5.6767  5.8941
33  0.8973  5.7947
53  2.6036  6.4965

## Use GeoViews to create map that shows the four cities in the itinerary

In [34]:
# Configure the map plot by using the itineraty_df
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    color="City",
    size = 100,
    frame_width = 400,
    frame_height = 400,
    alpha = 0.5)

In [35]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [36]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [37]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '75013d08dc434639a81412475839a6f1',
 'waypoints': '5.2741,-3.595|5.8941,5.6767|5.7947,0.8973|6.4965,2.6036'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [38]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()

route_response

{'features': [{'type': 'Feature',
   'properties': {'mode': 'drive',
    'waypoints': [{'location': [-3.595, 5.2741], 'original_index': 0},
     {'location': [5.6767, 5.8941], 'original_index': 1},
     {'location': [0.8973, 5.7947], 'original_index': 2},
     {'location': [2.6036, 6.4965], 'original_index': 3}],
    'units': 'metric',
    'distance': 2248532,
    'distance_units': 'meters',
    'time': 100503.414,
    'legs': [{'distance': 1295322,
      'time': 56120.964,
      'steps': [{'from_index': 0,
        'to_index': 6,
        'distance': 290,
        'time': 20.945,
        'instruction': {'text': 'Drive southeast.'}},
       {'from_index': 6,
        'to_index': 654,
        'distance': 54244,
        'time': 2195.016,
        'instruction': {'text': "Turn left onto A100/Route d'Aboisso. Continue on A100."}},
       {'from_index': 654,
        'to_index': 2280,
        'distance': 169705,
        'time': 7513.55,
        'instruction': {'text': 'Turn right to stay on A100.

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [39]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [40]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for step in legs:
    for direction in step:
        lat = direction[1]
        lng = direction[0]
        longitude.append(lng)
        latitude.append(lat)

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [41]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["Longitude"]=longitude
route_df["Latitude"]=latitude

# Display sample data
route_df.head()

Longitude  Latitude
0  -3.595032  5.274048
1  -3.594559  5.273760
2  -3.594245  5.273572
3  -3.593893  5.273354
4  -3.592991  5.272805

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [42]:
# Configure the route path by using the GeoViews' Path function
route_path = route_df.hvplot.paths(
    "Longitude",
    "Latitude",
    geo = True,
    tiles = "OSM",
    frame_width = 400,
    frame_height = 400,
    color = "red",
    line_width=3,
    alpha = 1
)

In [43]:
# Display a composed plot by using the route_map and route_path objects
route_path*itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    color="City",
    size = 100,
    frame_width = 400,
    frame_height = 400,
    alpha = 0.5)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Path.I   :Path   [Longitude,Latitude]
   .Points.I :Points   [Lng,Lat]   (City)